In [ ]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Acute_Myeloid_Leukemia"
cohort = "GSE222169"

# Input paths
in_trait_dir = "../../input/GEO/Acute_Myeloid_Leukemia"
in_cohort_dir = "../../input/GEO/Acute_Myeloid_Leukemia/GSE222169"

# Output paths
out_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/GSE222169.csv"
out_gene_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/gene_data/GSE222169.csv"
out_clinical_data_file = "../../output/preprocess/Acute_Myeloid_Leukemia/clinical_data/GSE222169.csv"
json_path = "../../output/preprocess/Acute_Myeloid_Leukemia/cohort_info.json"


### Step 1: Initial Data Loading

In [ ]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


### Step 2: Dataset Analysis and Clinical Feature Extraction

In [ ]:
import pandas as pd
import numpy as np
import os
import json
from typing import Optional, Callable, Dict, Any

# Examine the background information and sample characteristics
# 1. Gene Expression Data Availability
# Based on the series title "Mitochondrial fusion is a therapeutic vulnerability of acute myeloid leukemia"
# and the sample characteristics showing cell lines and patient samples with AML,
# this appears to be gene expression data rather than miRNA or methylation data.
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# Checking the sample characteristics dictionary for trait, age, and gender

# 2.1 Data Availability

# For trait (AML status)
# Row 0 contains 'cell line: MOLM-14', 'cell line: OCI-AML2', 'tissue source: patient with AML'
# All samples are AML samples (constant), but this is still useful for our trait identification
trait_row = 0  

# For age
# There's no age information available in the sample characteristics
age_row = None

# For gender
# There's no gender information available in the sample characteristics
gender_row = None

# 2.2 Data Type Conversion Functions

def convert_trait(value):
    """
    Convert trait values to binary format.
    1 = AML, 0 = Non-AML
    """
    if pd.isna(value):
        return None
    
    # Extract value after colon if it exists
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # All samples appear to be from AML cell lines or patients
    if 'AML' in value or 'leukemia' in value.lower():
        return 1
    return None  # Return None for uncertain cases

def convert_age(value):
    """
    Convert age values to continuous format.
    This function is not used since age data is not available.
    """
    return None

def convert_gender(value):
    """
    Convert gender values to binary format: 0 = female, 1 = male
    This function is not used since gender data is not available.
    """
    return None

# 3. Save Metadata - Initial Filtering
# Trait data is available since trait_row is not None
is_trait_available = trait_row is not None

validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
# Since trait_row is not None, we need to extract clinical features
if trait_row is not None:
    try:
        # Create a DataFrame from the sample characteristics dictionary provided in previous output
        sample_chars = {
            0: ['cell line: MOLM-14', 'cell line: OCI-AML2', 'tissue source: patient with AML'],
            1: ['cell type: leukemia cell line', 'genotype: OE_EMPTY', 'genotype: OE_MFN2', 'genotype: shCTL', 'genotype: shMFN2', 'genotype: shOPA1'],
            2: ['treatment: shCTL_72h', 'treatment: shMFN2_72h', None]
        }
        
        # Convert the dictionary to a DataFrame format compatible with geo_select_clinical_features
        # First, create a list of all unique sample IDs from all rows
        all_samples = []
        for row, values in sample_chars.items():
            for val in values:
                if val is not None and not pd.isna(val):
                    all_samples.append(val)
        
        # Create a DataFrame with samples as columns
        clinical_data = pd.DataFrame(index=range(len(sample_chars)), columns=all_samples)
        
        # Fill the DataFrame with sample values
        for row, values in sample_chars.items():
            for val in values:
                if val is not None and not pd.isna(val):
                    clinical_data.loc[row, val] = val
        
        # Extract clinical features
        selected_clinical = geo_select_clinical_features(
            clinical_df=clinical_data,
            trait=trait,
            trait_row=trait_row,
            convert_trait=convert_trait,
            age_row=age_row,
            convert_age=convert_age,
            gender_row=gender_row,
            convert_gender=convert_gender
        )
        
        # Preview the extracted clinical features
        preview = preview_df(selected_clinical)
        print("Preview of selected clinical features:")
        print(preview)
        
        # Save the extracted clinical features
        os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
        selected_clinical.to_csv(out_clinical_data_file)
        print(f"Clinical data saved to {out_clinical_data_file}")
    except Exception as e:
        print(f"Error extracting clinical features: {e}")
        print("Clinical data extraction was skipped due to an error.")


### Step 3: Gene Data Extraction

In [ ]:
# 1. Use the get_genetic_data function from the library to get the gene_data from the matrix_file previously defined.
gene_data = get_genetic_data(matrix_file)

# 2. Print the first 20 row IDs (gene or probe identifiers) for future observation.
print(gene_data.index[:20])


### Step 4: Gene Identifier Review

In [ ]:
# These identifiers ("TC0100006437.hg.1", etc.) are not standard human gene symbols
# They appear to be probe IDs from a microarray platform, likely Affymetrix or Thermo Fisher
# These need to be mapped to standard gene symbols for biological interpretation

requires_gene_mapping = True


### Step 5: Gene Annotation

In [ ]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


### Step 6: Gene Identifier Mapping

In [ ]:
# Looking at the gene annotation dictionary and the gene identifiers in the expression data
# The 'ID' column in gene_annotation matches the index in gene_data (e.g., "TC0100006437.hg.1")
# The gene symbols need to be extracted from the 'SPOT_ID.1' column which contains detailed annotation information

# 1. Determine the columns for mapping
prob_col = 'ID'  # This column contains the probe IDs matching our gene expression data
gene_col = 'SPOT_ID.1'  # This column contains gene information including symbols

# 2. Get the gene mapping dataframe
mapping_df = get_gene_mapping(gene_annotation, prob_col, gene_col)

# 3. Apply gene mapping to convert probe measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, mapping_df)

# Preview the first few rows of the gene expression data after mapping
print("Preview of gene expression data after mapping:")
print(gene_data.head())
print("Number of genes in the mapped data:", len(gene_data))


### Step 7: Data Normalization and Linking

In [ ]:
# 1. Normalize the obtained gene data with the 'normalize_gene_symbols_in_index' function from the library.
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# 2. Analyze the clinical data structure more carefully
print("Clinical data shape:", clinical_data.shape)
print("Clinical data columns:", clinical_data.columns)
print("Clinical data index:", clinical_data.index)

# Examine the first few rows to understand the data structure
print("First few rows of clinical data:")
print(clinical_data.iloc[:, :5].head())  # Show only first 5 columns for brevity

# Extract relevant information for creating a more appropriate clinical feature dataframe
# Based on the GSE series information, this dataset is about mitochondrial fusion in AML
# We'll create a new clinical data approach by directly processing column names

# Get sample IDs from the gene expression data
sample_ids = normalized_gene_data.columns.tolist()

# Create a trait dataframe using the GSM IDs as sample identifiers
# Since we're interested in MFN2 treatment effects, we'll use column names that contain relevant identifiers
trait_values = []
for sample_id in sample_ids:
    # Default to None
    trait_value = None
    
    # Check if the sample ID is in clinical_data columns
    if sample_id in clinical_data.columns:
        # Look at the treatment row (index 2)
        cell_value = clinical_data.loc[2, sample_id]
        if isinstance(cell_value, str):
            if 'shMFN2' in cell_value:
                trait_value = 1
            elif 'shCTL' in cell_value:
                trait_value = 0
    
    trait_values.append(trait_value)

# Create a DataFrame with the trait values
trait_df = pd.DataFrame({trait: trait_values}, index=sample_ids)
print("Trait dataframe preview:")
print(trait_df.head())

# Save the clinical data
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
trait_df.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# Link the clinical and genetic data
linked_data = pd.concat([trait_df.T, normalized_gene_data], axis=0)
print(f"Linked data shape: {linked_data.shape}")

# Handle missing values in the linked data
linked_data = handle_missing_values(linked_data, trait)
print(f"Data shape after handling missing values: {linked_data.shape}")

# If we still have data after handling missing values
if linked_data.shape[0] > 0:
    # Determine whether the trait and some demographic features are severely biased
    is_trait_biased, unbiased_linked_data = judge_and_remove_biased_features(linked_data, trait)

    # Conduct quality check and save the cohort information
    note = "Dataset contains AML cell lines with different treatments. Trait was defined as shMFN2 knockdown (1) vs shCTL control (0)."
    is_usable = validate_and_save_cohort_info(
        is_final=True, 
        cohort=cohort, 
        info_path=json_path, 
        is_gene_available=True, 
        is_trait_available=True, 
        is_biased=is_trait_biased, 
        df=unbiased_linked_data,
        note=note
    )

    # If the linked data is usable, save it
    if is_usable:
        os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
        unbiased_linked_data.to_csv(out_data_file)
        print(f"Processed dataset saved to {out_data_file}")
    else:
        print("Dataset not usable due to bias in trait distribution. Data not saved.")
else:
    # Record that this dataset is not usable due to insufficient trait data
    validate_and_save_cohort_info(
        is_final=True,
        cohort=cohort,
        info_path=json_path,
        is_gene_available=True,
        is_trait_available=False,
        is_biased=None,
        df=pd.DataFrame(),
        note="No samples with valid trait values remained after filtering"
    )
    print("Dataset marked as not usable due to insufficient trait data after filtering.")